In [1]:
!pip install pandas
import json
import requests
import urllib3
import threading
import pandas as pd
import numpy as np
from sseclient import SSEClient
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, accuracy_score

# --- Configurare Client Stream ---
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)
API_KEY = "cd799bc7b34466ffd41b040fad08d30cd4543ed02115fc7efc72219d3a2ea8ee"
STREAM_URL = "https://95.217.75.14:8443/stream"
FLAG_URL = "https://95.217.75.14:8443/api/flag"
headers = {"X-API-Key": API_KEY}

# --- Configurare Model ---
model = None
encoders = {}
FEATURES_TO_USE = [
    'amt', 'lat', 'long', 'merch_lat', 'merch_long',
    'job', 'category', 'merchant',
    'hour', 'hour_fraud_level', 'hour_fraud_rate_level'
]
CATEGORICAL_COLS = ['job', 'category', 'merchant', 'hour_fraud_level', 'hour_fraud_rate_level']


[notice] A new release of pip is available: 25.0.1 -> 25.3
[notice] To update, run: C:\Users\claud\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


Defaulting to user installation because normal site-packages is not writeable


In [3]:
# --- Funcții Helper pentru Model ---
def hour_fraud_level(h):
    if h in [22, 23]: return 'mare'
    elif h in [0, 1, 2, 3]: return 'mediu'
    else: return 'mic'

def hour_fraud_rate_level(h):
    if h in [12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23]: return 'mare'
    elif h in [0, 1, 2, 3]: return 'mediu'
    else: return 'mic'

def safe_label_encode(col_name, value):
    global encoders
    try:
        le = encoders[col_name]
        return le.transform([value])[0]
    except (ValueError, KeyError):
        return -1 # Valoare necunoscută

# --- Funcția de Antrenare ---
def train_model_globally():
    global model, encoders
    print("--- Începe antrenarea modelului (o singură dată) ---")
    try:
        df = pd.read_csv('hackathon_train.csv', sep='|')
    except FileNotFoundError:
        print("EROARE: Fișierul 'hackathon_train.csv' nu a fost găsit.")
        return

    X = df.drop(columns=['is_fraud'])
    y = df['is_fraud']
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
    print(f"Set de date încărcat. Antrenare pe {len(X_train)} eșantioane.")

    print("Antrenarea encoderelor pentru coloanele categorice...")
    for dataset in [X_train, X_test]:
        dataset['hour'] = pd.to_datetime(dataset['trans_time'], format='%H:%M:%S', errors='coerce').dt.hour
        dataset['hour_fraud_level'] = dataset['hour'].apply(hour_fraud_level)
        dataset['hour_fraud_rate_level'] = dataset['hour'].apply(hour_fraud_rate_level)

    for col in CATEGORICAL_COLS:
        le = LabelEncoder()
        X_train[col] = le.fit_transform(X_train[col].astype(str))
        encoders[col] = le
        
        # Gestionare valori necunoscute în X_test (pentru validare)
        X_test[col] = X_test[col].astype(str).map(lambda s: s if s in le.classes_ else '<unknown>')
        le_classes = le.classes_.tolist()
        if '<unknown>' not in le_classes:
            le_classes.append('<unknown>')
        le.classes_ = np.array(le_classes)
        X_test[col] = le.transform(X_test[col])

    print("Antrenarea modelului RandomForest...")
    model = RandomForestClassifier(n_estimators=100, random_state=42, class_weight='balanced')
    model.fit(X_train[FEATURES_TO_USE], y_train)
    print("Model antrenat.")
    
    y_pred_local = model.predict(X_test[FEATURES_TO_USE])
    acc = accuracy_score(y_test, y_pred_local)
    print(f"\nVerificare model (local): Acuratețe pe setul de test: {acc:.4f}")
    print("--- Antrenare finalizată. ---")

# --- Funcții Client Stream ---
def flag_transaction(trans_num, flag_value):
    try:
        payload = {"trans_num": trans_num, "flag_value": flag_value}
        response = requests.post(FLAG_URL, headers=headers, json=payload, verify=False, timeout=10)
        response.raise_for_status()
        return response.json()
    except Exception as e:
        print(f"Eroare la semnalarea tranzacției {trans_num}: {e}")
        return None

def process_transaction(transaction):
    global model, encoders
    try:
        trans_num = transaction.get('trans_num')
        if not trans_num: return

        features_dict = {}
        try:
            hour = pd.to_datetime(transaction.get('trans_time'), format='%H:%M:%S', errors='coerce').hour
        except Exception: hour = 0
        
        features_dict['hour'] = hour
        features_dict['hour_fraud_level'] = hour_fraud_level(hour)
        features_dict['hour_fraud_rate_level'] = hour_fraud_rate_level(hour)

        for col in FEATURES_TO_USE:
            if col not in features_dict:
                features_dict[col] = transaction.get(col, 0)

        feature_vector = []
        for col in FEATURES_TO_USE:
            value = features_dict[col]
            if col in CATEGORICAL_COLS:
                encoded_val = safe_label_encode(col, str(value))
                feature_vector.append(encoded_val)
            else:
                try: feature_vector.append(float(value))
                except (ValueError, TypeError): feature_vector.append(0.0)

        prediction = model.predict([feature_vector])
        is_fraud = int(prediction[0])

        print(f"Procesat {trans_num}: Suma ${transaction.get('amt')}, Cat {transaction.get('category')}, Predicție: {is_fraud}")
        
        result = flag_transaction(trans_num, is_fraud)
        if result:
            print(f"Răspuns server pentru {trans_num}: {result}")
        print("-" * 80)
    except Exception as e:
        print(f"Eroare la procesarea tranzacției {transaction.get('trans_num')}: {e}")

In [4]:
# 1. Antrenăm modelul și encoderele o singură dată
train_model_globally()

--- Începe antrenarea modelului (o singură dată) ---
Set de date încărcat. Antrenare pe 592009 eșantioane.
Antrenarea encoderelor pentru coloanele categorice...
Antrenarea modelului RandomForest...
Model antrenat.

Verificare model (local): Acuratețe pe setul de test: 0.9663
--- Antrenare finalizată. ---


In [ ]:
# 2. Ne conectăm la stream
try:
    print("Se conectează la stream...")
    
    # Inițializăm clientul SSE
    client = SSEClient(STREAM_URL, headers=headers, verify=False)
    
    print("Conectat la stream. Se așteaptă tranzacții...")

    # Iterăm direct peste 'client'
    for event in client:
        try:
            if event.data:
                transaction = json.loads(event.data)
                
                # Procesăm fiecare tranzacție într-un thread nou
                thread = threading.Thread(target=process_transaction, args=(transaction,))
                thread.start()
        except json.JSONDecodeError as e:
            print(f"Eroare la parsarea JSON din stream: {e}")
        except Exception as e:
            print(f"Eroare la gestionarea evenimentului: {e}")

except requests.exceptions.RequestException as e:
    print(f"Eroare de conexiune la stream: {e}")
except KeyboardInterrupt:
    print("\nOprit de utilizator.")
except Exception as e:
    print(f"Eroare neașteptată: {e}")

Se conectează la stream...
Conectat la stream. Se așteaptă tranzacții...
Procesat 0b51340834bd3a6b716038e49ad48d77: Suma $11.89, Cat grocery_pos, Predicție: 1


C:\Users\claud\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


Răspuns server pentru 0b51340834bd3a6b716038e49ad48d77: {'success': True, 'reason': 'Response recorded successfully'}
--------------------------------------------------------------------------------


C:\Users\claud\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


Procesat 5193d704e26b170098b5c054e1756d4f: Suma $122.9, Cat grocery_pos, Predicție: 0
Răspuns server pentru 5193d704e26b170098b5c054e1756d4f: {'success': True, 'reason': 'Response recorded successfully'}
--------------------------------------------------------------------------------


...

Procesat 3b938f582d5b69e85e3b44102e2967cb: Suma $211.46, Cat misc_pos, Predicție: 0
Răspuns server pentru 3b938f582d5b69e85e3b44102e2967cb: {'success': True, 'reason': 'Response recorded successfully'}
--------------------------------------------------------------------------------


C:\Users\claud\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


Procesat 6bbc6d81a772a4cc38579bddea8d4ffb: Suma $76.22, Cat misc_net, Predicție: 0
Răspuns server pentru 6bbc6d81a772a4cc38579bddea8d4ffb: {'success': True, 'reason': 'Response recorded successfully'}
--------------------------------------------------------------------------------


C:\Users\claud\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


Procesat 9c657329084571a3e5ad6eff45f8ab4e: Suma $108.32, Cat shopping_net, Predicție: 0
Răspuns server pentru 9c657329084571a3e5ad6eff45f8ab4e: {'success': True, 'reason': 'Response recorded successfully'}
--------------------------------------------------------------------------------
